using the cohere for embeddings and pinecone as the vectore db

In [16]:
import os
import voyageai
from dotenv import load_dotenv
load_dotenv()
import cohere
from pinecone import Pinecone
from langchain_text_splitters import RecursiveCharacterTextSplitter
import fitz
from langchain.schema import Document
from docx import Document as DocxDocument

In [19]:
#get the file path from local disk
import os
file_path=r"/home/spencer/Downloads/ANGELA CHACHA PROJECT REPORT (1).docx"
if os.path.exists(file_path):
    print("File exists")
    if file_path.endswith(".pdf"):
        doc=fitz.open(file_path)
        data=" "
        for page in doc:
            data+=page.get_text()
        doc.close
    else:
        doc=DocxDocument(file_path)
        list_data=[]
        for paragraph in doc.paragraphs:
            list_data.append(paragraph.text)
        data='\n'.join(list_data)

else:
    print("file does not exist")

data






File exists


"\nSCHOOL OF PURE AND APPLIED SCIENCES\nDEPARTMENT OF COMPUTING AND INFORMATION SCIENCES\n\nSCO: 400 PROJECT\nBREAST CANCER DETECTION SYSTEM\n\nCHACHA SUSAN ANGELA\nJ17/5122/2021\n\nSUPERVISOR\nDR. BERNARD ONDARA\n\n\nTHIS PROJECT PROPOSAL IS SUBMITTED FOR THE PARTIAL FULFILLMENT OF THE REQUIREMENTS FOR THE AWARD OF THE DEGREE OF BACHELOR IN COMPUTER SCIENCE IN THE SCHOOL OF PURE AND APPLIED SCIENCES OF KENYATTA UNIVERSITY\n\n\n\n\n\n\nMARCH, 2025\n\nDECLARATION\nI declare that this proposal is my original work and has not been presented in any other university/institution for consideration for any degree award. This proposal has been complemented and referenced sources duly cited using the APA 7 system and by anti-plagiarism regulations.\n\nSignature…………………………………………                        Date……………………............\n\nSupervisor’s declaration:\n\nSignature…………………………………………                        Date……………………............\n\n\n\n\nChacha Susan Angela\nDepartment of Computing and Informatio

In [3]:
# loading data from an xml file
import requests
import xml.etree.ElementTree as ET
from bs4 import BeautifulSoup

def extract_from_xml_url(url):
    try:
        response=requests.get(url) #gets the url
        response.raise_for_status # raise for any exceptions
        print(f"response :{response}")
        soup=BeautifulSoup(response.content,'xml') #for easier extraction
        print(f"soup : {soup}")

        #extract all texts
        all_texts=[]
        text=soup.get_text(separator=' ',strip=True)
        all_texts.append(text)
        print(f"all texts :{all_texts}")

        return all_texts

    except Exception as e:
        print (f"error processing the xml file {e}")
        return []  

In [6]:
url=os.environ['URL']
docs=extract_from_xml_url(url)

NameError: name 'extract_from_xml_url' is not defined

In [ ]:
text_splitter=RecursiveCharacterTextSplitter(chunk_size=1500 ,
                                              chunk_overlap=200,
                                              length_function=lambda text: len(text.split())) #length function make the model split documents based on the tokens hence can help you to stay on the token limit
#chuncking the texts-- gets character by character like 'a' '1'
def chunk_documents(docs):
    all_chunks=[]
    for doc in docs:
        chunks=text_splitter.split_text(doc)
        all_chunks.extend(chunks)
    # texts=text_splitter.split_documents(docs)
    return all_chunks

def text_chunk_document(data):
    documents=[Document(page_content=data,metadata={"source":"pdf"} )]
    all_chunks=text_splitter.split_documents(documents)
    print("all_chunks",all_chunks)
    return all_chunks

text_chunk_document(data)



all_chunks [Document(metadata={'source': 'pdf'}, page_content='SCHOOL OF PURE AND APPLIED SCIENCES\nDEPARTMENT OF COMPUTING AND INFORMATION SCIENCES\n\nSCO: 400 PROJECT\nBREAST CANCER DETECTION SYSTEM\n\nCHACHA SUSAN ANGELA\nJ17/5122/2021\n\nSUPERVISOR\nDR. BERNARD ONDARA\n\n\nTHIS PROJECT PROPOSAL IS SUBMITTED FOR THE PARTIAL FULFILLMENT OF THE REQUIREMENTS FOR THE AWARD OF THE DEGREE OF BACHELOR IN COMPUTER SCIENCE IN THE SCHOOL OF PURE AND APPLIED SCIENCES OF KENYATTA UNIVERSITY\n\n\n\n\n\n\nMARCH, 2025\n\nDECLARATION\nI declare that this proposal is my original work and has not been presented in any other university/institution for consideration for any degree award. This proposal has been complemented and referenced sources duly cited using the APA 7 system and by anti-plagiarism regulations.\n\nSignature…………………………………………                        Date……………………............\n\nSupervisor’s declaration:\n\nSignature…………………………………………                        Date……………………............\n\n\n\n\

[Document(metadata={'source': 'pdf'}, page_content='SCHOOL OF PURE AND APPLIED SCIENCES\nDEPARTMENT OF COMPUTING AND INFORMATION SCIENCES\n\nSCO: 400 PROJECT\nBREAST CANCER DETECTION SYSTEM\n\nCHACHA SUSAN ANGELA\nJ17/5122/2021\n\nSUPERVISOR\nDR. BERNARD ONDARA\n\n\nTHIS PROJECT PROPOSAL IS SUBMITTED FOR THE PARTIAL FULFILLMENT OF THE REQUIREMENTS FOR THE AWARD OF THE DEGREE OF BACHELOR IN COMPUTER SCIENCE IN THE SCHOOL OF PURE AND APPLIED SCIENCES OF KENYATTA UNIVERSITY\n\n\n\n\n\n\nMARCH, 2025\n\nDECLARATION\nI declare that this proposal is my original work and has not been presented in any other university/institution for consideration for any degree award. This proposal has been complemented and referenced sources duly cited using the APA 7 system and by anti-plagiarism regulations.\n\nSignature…………………………………………                        Date……………………............\n\nSupervisor’s declaration:\n\nSignature…………………………………………                        Date……………………............\n\n\n\n\nChacha Sus

In [21]:
# vo=voyageai.Client(api_key=os.environ["VOYAGE_API_KEY"])
co=cohere.ClientV2(os.environ["COHERE_API_KEY"])


In [22]:
#generate embeddings for text
def generate_embeddings(text):
    # embeddings=vo.embed(text,model="voyage-3-large", input_type="document")
    embeddings=co.embed(texts=text, model="embed-english-v3.0",input_type="search_document",embedding_types=["float"])
    return embeddings.embeddings.float[0]

chunked_data=text_chunk_document(data)
texts=[doc.page_content for doc in chunked_data]
generate_embeddings(texts)




all_chunks [Document(metadata={'source': 'pdf'}, page_content='SCHOOL OF PURE AND APPLIED SCIENCES\nDEPARTMENT OF COMPUTING AND INFORMATION SCIENCES\n\nSCO: 400 PROJECT\nBREAST CANCER DETECTION SYSTEM\n\nCHACHA SUSAN ANGELA\nJ17/5122/2021\n\nSUPERVISOR\nDR. BERNARD ONDARA\n\n\nTHIS PROJECT PROPOSAL IS SUBMITTED FOR THE PARTIAL FULFILLMENT OF THE REQUIREMENTS FOR THE AWARD OF THE DEGREE OF BACHELOR IN COMPUTER SCIENCE IN THE SCHOOL OF PURE AND APPLIED SCIENCES OF KENYATTA UNIVERSITY\n\n\n\n\n\n\nMARCH, 2025\n\nDECLARATION\nI declare that this proposal is my original work and has not been presented in any other university/institution for consideration for any degree award. This proposal has been complemented and referenced sources duly cited using the APA 7 system and by anti-plagiarism regulations.\n\nSignature…………………………………………                        Date……………………............\n\nSupervisor’s declaration:\n\nSignature…………………………………………                        Date……………………............\n\n\n\n\

[-0.007827759,
 0.001958847,
 -0.014465332,
 -0.006389618,
 -0.02267456,
 6.347895e-05,
 -0.029312134,
 -0.025100708,
 0.040924072,
 0.02381897,
 -0.014083862,
 -0.03152466,
 0.0736084,
 -0.047851562,
 0.021774292,
 0.013000488,
 0.018127441,
 0.05407715,
 0.071899414,
 0.002840042,
 -0.007358551,
 0.007297516,
 0.06402588,
 0.008354187,
 0.00037574768,
 0.023452759,
 -0.076660156,
 0.002319336,
 -0.04800415,
 -0.0058517456,
 -0.014602661,
 0.04827881,
 0.024383545,
 0.03189087,
 -0.0390625,
 0.006580353,
 -0.04071045,
 0.039489746,
 -0.020141602,
 0.03086853,
 0.02508545,
 -0.017959595,
 0.09338379,
 -0.02798462,
 0.02003479,
 -0.0045700073,
 0.028427124,
 -0.025802612,
 0.04345703,
 0.03378296,
 -0.0013599396,
 0.047454834,
 -0.012817383,
 0.0033931732,
 0.00674057,
 0.010856628,
 -0.03427124,
 -0.0063438416,
 0.008003235,
 0.07330322,
 0.021499634,
 0.017440796,
 -0.01902771,
 -0.05065918,
 -0.03765869,
 -0.016998291,
 0.015563965,
 0.027145386,
 0.020339966,
 -0.009735107,
 0.01070

In [8]:
#generate embeddings for questions
def query_embeddings(query):
    q_embeddings=co.embed(texts=[query],model="embed-english-v3.0",input_type="search_query",embedding_types=["float"])
    return q_embeddings.embeddings.float[0]

In [12]:
import time

texts = chunk_documents(docs)
max_tokens_per_min = 95000   # Stay under 100K to be safe
max_tokens_per_batch = 30000 # Optional: keep single batch small
batch = []
max_texts_per_batch = 96
batch_token_total = 0
all_embeddings = []

def get_token_count(text):
    return len(co.tokenize(text=text, model="embed-english-v3.0").tokens)



start_time = time.time()

for idx, text in enumerate(texts):
    tokens = get_token_count(text)
    
    # If adding this text exceeds the per-batch token limit, send batch
    if (batch_token_total + tokens > max_tokens_per_batch or len(batch) >= max_texts_per_batch):
        print(f"Sending batch of {len(batch)} texts with {batch_token_total} tokens")
        batch_embeddings = generate_embeddings(batch)
        all_embeddings.extend(batch_embeddings)
        
        batch = []
        batch_token_total = 0

        # Check elapsed time to respect rate limit
        elapsed = time.time() - start_time
        if elapsed < 60:
            print(f"Waiting {60 - elapsed:.1f}s to stay under rate limit...")
            time.sleep(60 - elapsed)
        start_time = time.time()
    
    # Add text to current batch
    batch.append(text)
    batch_token_total += tokens

# the final batch
if batch:
    print(f"Sending final batch of {len(batch)} texts with {batch_token_total} tokens")
    batch_embeddings = generate_embeddings(batch)
    all_embeddings.extend(batch_embeddings)


Sending batch of 74 texts with 29780 tokens
Waiting 50.9s to stay under rate limit...
Sending batch of 69 texts with 29568 tokens
Waiting 58.0s to stay under rate limit...
Sending batch of 73 texts with 29882 tokens
Waiting 56.7s to stay under rate limit...
Sending batch of 78 texts with 29830 tokens
Waiting 57.5s to stay under rate limit...
Sending batch of 78 texts with 29920 tokens
Waiting 57.6s to stay under rate limit...
Sending batch of 65 texts with 29732 tokens
Waiting 55.3s to stay under rate limit...
Sending batch of 73 texts with 29461 tokens
Waiting 57.7s to stay under rate limit...
Sending batch of 86 texts with 29876 tokens
Waiting 51.8s to stay under rate limit...
Sending batch of 96 texts with 29258 tokens
Waiting 57.0s to stay under rate limit...
Sending batch of 89 texts with 29778 tokens
Waiting 56.7s to stay under rate limit...
Sending batch of 71 texts with 29924 tokens
Waiting 57.6s to stay under rate limit...
Sending batch of 91 texts with 29967 tokens
Waiting 52

In [ ]:
#function to chunk the text and generate embeddings
import time
embeddings=[]
texts=chunk_documents(docs)
for i, text in enumerate(texts):
    tokens = co.tokenize(text=text, model="embed-english-v3.0").tokens
    print(f"Text {i+1}: {len(tokens)} tokens")

batch_size =50
for i in range(0,len(texts),batch_size):
    batch=texts[i:i+batch_size]
    batch_embedding=generate_embeddings(batch)
    embeddings.append(batch_embedding)
    time.sleep(2)

In [ ]:
#testing the similariy using cosine
from numpy import dot
from numpy.linalg import norm
query="what does the mediterenian diet emphasize on?"
doc_embedds=embeddings
q_embeddings=query_embeddings(query)
similarity=dot(doc_embedds,q_embeddings)/(norm(doc_embedds)*norm(q_embeddings))
print(f"Similarity : {similarity}")

Similarity : [0.24762685 0.08435089 0.05709943 0.09577442 0.02234798 0.06167636]


In [14]:
def generate_embedded_doc(embeddings,data):
    finaldoc=[]
    for i, (embedding,data) in enumerate(zip(embeddings, data)):
        doc={
            "id":str(i),
            "values":embedding,
            "metadata":{
                'text':data,
                'chunk_index':i,
                'source':'custom text'
            }       
              }
        finaldoc.append(doc)
    return finaldoc

In [15]:
embedding_dim=1024

total_floates=len(all_embeddings)
num_embeddings=total_floates//embedding_dim
print(f"totalfloats: {total_floates}, num_embeddings:{num_embeddings}")


reshaped_embeddings=[]
for i in range(0,len(all_embeddings),embedding_dim):
    embedding_vector=all_embeddings[i:i+embedding_dim]
    reshaped_embeddings.append(embedding_vector)
    
reshaped_embeddings

totalfloats: 99328, num_embeddings:97


[[0.00034618378,
  -0.022613525,
  -0.0014772415,
  -0.004272461,
  -0.019454956,
  -0.01158905,
  0.0143585205,
  -0.015434265,
  -0.037628174,
  0.045013428,
  -0.005973816,
  0.041290283,
  0.011749268,
  -0.010032654,
  0.0031929016,
  -0.009170532,
  0.04058838,
  0.008132935,
  0.048828125,
  0.007785797,
  0.0029239655,
  0.031234741,
  0.030410767,
  0.027496338,
  -0.008995056,
  -0.009315491,
  -0.025909424,
  -0.005584717,
  -0.038635254,
  -0.051727295,
  -0.010498047,
  0.07946777,
  -0.008148193,
  0.020019531,
  -0.004524231,
  -0.0031375885,
  0.029769897,
  0.014503479,
  0.020187378,
  0.022216797,
  0.014732361,
  -0.02015686,
  0.039367676,
  0.011070251,
  0.037017822,
  -0.029037476,
  0.003107071,
  -0.10168457,
  0.038269043,
  0.022567749,
  0.0022678375,
  0.029159546,
  -0.012817383,
  0.013938904,
  -0.0018205643,
  0.008964539,
  0.059295654,
  -0.081970215,
  0.042938232,
  -0.015945435,
  -0.04046631,
  -0.05621338,
  0.05279541,
  -0.031097412,
  -0.0221

In [16]:
records_with_embeddings=generate_embedded_doc(reshaped_embeddings,texts)

In [18]:
pc=Pinecone(api_key=os.environ["PINECONE_API_KEY"])
index=pc.Index(os.environ['PINECONE_INDEX'])

In [19]:
records_with_embeddings

[{'id': '0',
  'values': [0.00034618378,
   -0.022613525,
   -0.0014772415,
   -0.004272461,
   -0.019454956,
   -0.01158905,
   0.0143585205,
   -0.015434265,
   -0.037628174,
   0.045013428,
   -0.005973816,
   0.041290283,
   0.011749268,
   -0.010032654,
   0.0031929016,
   -0.009170532,
   0.04058838,
   0.008132935,
   0.048828125,
   0.007785797,
   0.0029239655,
   0.031234741,
   0.030410767,
   0.027496338,
   -0.008995056,
   -0.009315491,
   -0.025909424,
   -0.005584717,
   -0.038635254,
   -0.051727295,
   -0.010498047,
   0.07946777,
   -0.008148193,
   0.020019531,
   -0.004524231,
   -0.0031375885,
   0.029769897,
   0.014503479,
   0.020187378,
   0.022216797,
   0.014732361,
   -0.02015686,
   0.039367676,
   0.011070251,
   0.037017822,
   -0.029037476,
   0.003107071,
   -0.10168457,
   0.038269043,
   0.022567749,
   0.0022678375,
   0.029159546,
   -0.012817383,
   0.013938904,
   -0.0018205643,
   0.008964539,
   0.059295654,
   -0.081970215,
   0.042938232,
   

In [20]:
index.upsert(vectors=records_with_embeddings)

{'upserted_count': 97}